# Airbnb Data analysis

##### Submitted By - Harsimran Kaur - 609078

#### Case Study - Airbnb
Airbnb is an online marketplace that connects people who want to rent out their homes with people looking for accommodations in that locale. NYC is the most populous city in the United States, and one of the most popular tourism and business places globally. Since 2008, guests and hosts have used Airbnb to expand on traveling possibilities and present a more unique, personalized way of experiencing the world. Nowadays, Airbnb became one of a kind service that is used by the whole world. Data analysts become a crucial factor for the company that provided millions of listings through Airbnb. These listings generate a lot of data that can be analyzed and used for security, business decisions, understanding of customers’ and providers’ behavior on the platform, implementing innovative additional services, guiding marketing initiatives, and much more.

![Airbnb Image](files/tables/108130_Airbnb__Invested__10_mn_In_100_Absurd_Buildings3.jpg)

#### Importing the required libraries and creating a pyspark session

In [0]:
from pyspark.sql import SparkSession
spark = SparkSession.builder.appName("airbnb").getOrCreate()

#### Reading the “New York Airbnb Open Data” as csv file

In [0]:
nyc_df = spark.read.csv('dbfs:/FileStore/shared_uploads/harsimran.kaur@incedoinc.com/AB_NYC_2019.csv',header=True,inferSchema=True)

### Knowing about the data

#### 1) Data snapshot

In [0]:
nyc_df.toPandas().head(7)

id 
 name 
 host_id 
 host_name 
 neighbourhood_group 
 neighbourhood 
 latitude 
 longitude 
 room_type 
 price 
 minimum_nights 
 number_of_reviews 
 last_review 
 reviews_per_month 
 calculated_host_listings_count 
 availability_365 
 
 
 
 
 0 
 2539 
 Clean & quiet apt home by the park 
 2787 
 John 
 Brooklyn 
 Kensington 
 40.64749 
 -73.97237 
 Private room 
 149 
 1 
 9 
 2018-10-19 
 0.21 
 6 
 365.0 
 
 
 1 
 2595 
 Skylit Midtown Castle 
 2845 
 Jennifer 
 Manhattan 
 Midtown 
 40.75362 
 -73.98377 
 Entire home/apt 
 225 
 1 
 45 
 2019-05-21 
 0.38 
 2 
 355.0 
 
 
 2 
 3647 
 THE VILLAGE OF HARLEM....NEW YORK ! 
 4632 
 Elisabeth 
 Manhattan 
 Harlem 
 40.80902 
 -73.9419 
 Private room 
 150 
 3 
 0 
 None 
 None 
 1 
 365.0 
 
 
 3 
 3831 
 Cozy Entire Floor of Brownstone 
 4869 
 LisaRoxanne 
 Brooklyn 
 Clinton Hill 
 40.68514 
 -73.95976 
 Entire home/apt 
 89 
 1 
 270 
 2019-07-05 
 4.64 
 1 
 194.0 
 
 
 4 
 5022 
 Entire Apt: Spacious Studio/Loft by central park 
 7192 
 Laura 
 Manhattan 
 East Harlem 
 40.79851 
 -73.94399 
 Entire home/apt 
 80 
 10 
 9 
 2018-11-19 
 0.10 
 1 
 0.0 
 
 
 5 
 5099 
 Large Cozy 1 BR Apartment In Midtown East 
 7322 
 Chris 
 Manhattan 
 Murray Hill 
 40.74767 
 -73.975 
 Entire home/apt 
 200 
 3 
 74 
 2019-06-22 
 0.59 
 1 
 129.0 
 
 
 6 
 5121 
 BlissArtsSpace! 
 7356 
 Garon 
 Brooklyn 
 Bedford-Stuyvesant 
 40.68688 
 -73.95596 
 Private room 
 60 
 45 
 49 
 2017-10-05 
 0.40 
 1 
 0.0

In [0]:
type(nyc_df)

Out[4]: pyspark.sql.dataframe.DataFrame

#### 2) Volume of data

In [0]:
rows=nyc_df.count()
cols=len(nyc_df.columns)
print("No. of rows in data: ",rows)
print("No. of columns in data: ",cols)

No. of rows in data:  49079
No. of columns in data:  16


#### 3) Names of columns

In [0]:
for i in nyc_df.columns:
    print(i)

id
name
host_id
host_name
neighbourhood_group
neighbourhood
latitude
longitude
room_type
price
minimum_nights
number_of_reviews
last_review
reviews_per_month
calculated_host_listings_count
availability_365


#### 4) Data Schema

In [0]:
nyc_df.printSchema()

root
 |-- id: string (nullable = true)
 |-- name: string (nullable = true)
 |-- host_id: string (nullable = true)
 |-- host_name: string (nullable = true)
 |-- neighbourhood_group: string (nullable = true)
 |-- neighbourhood: string (nullable = true)
 |-- latitude: string (nullable = true)
 |-- longitude: string (nullable = true)
 |-- room_type: string (nullable = true)
 |-- price: string (nullable = true)
 |-- minimum_nights: string (nullable = true)
 |-- number_of_reviews: string (nullable = true)
 |-- last_review: string (nullable = true)
 |-- reviews_per_month: string (nullable = true)
 |-- calculated_host_listings_count: string (nullable = true)
 |-- availability_365: integer (nullable = true)



#### 5) Number of null values in each column

In [0]:
from pyspark.sql.functions import col,isnan, when, count
null_df=nyc_df.select([count(when(isnan(c) | col(c).isNull(), c)).alias(c) for c in nyc_df.columns])
null_df.toPandas().head()

id 
 name 
 host_id 
 host_name 
 neighbourhood_group 
 neighbourhood 
 latitude 
 longitude 
 room_type 
 price 
 minimum_nights 
 number_of_reviews 
 last_review 
 reviews_per_month 
 calculated_host_listings_count 
 availability_365 
 
 
 
 
 0 
 0 
 32 
 185 
 212 
 185 
 185 
 185 
 185 
 185 
 185 
 185 
 205 
 10234 
 10215 
 187 
 342

# Data cleaning and preprocessing

#### 1) Dropping the rows with null values

In [0]:
nyc_df2=nyc_df.na.drop(how="any")
print("No. of rows in data without null_values = ",nyc_df2.count())

No. of rows in data without null_values =  38685


#### 2) Number of rows with null values after dropping null values

In [0]:
no_null_df=nyc_df2.select([count(when(isnan(c) | col(c).isNull(), c)).alias(c) for c in nyc_df2.columns])
no_null_df.toPandas().head()

id 
 name 
 host_id 
 host_name 
 neighbourhood_group 
 neighbourhood 
 latitude 
 longitude 
 room_type 
 price 
 minimum_nights 
 number_of_reviews 
 last_review 
 reviews_per_month 
 calculated_host_listings_count 
 availability_365 
 
 
 
 
 0 
 0 
 0 
 0 
 6 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0

#### 3) Type casting according to data

In [0]:
nyc_df2=nyc_df2.withColumn("price",nyc_df2.price.cast("int"))
nyc_df2=nyc_df2.withColumn("id",nyc_df2.id.cast("int"))
nyc_df2=nyc_df2.withColumn("host_id",nyc_df2.host_id.cast("int"))
nyc_df2=nyc_df2.withColumn("minimum_nights",nyc_df2.minimum_nights.cast("int"))
nyc_df2=nyc_df2.withColumn("number_of_reviews",nyc_df2.number_of_reviews.cast("int"))
nyc_df2=nyc_df2.withColumn("reviews_per_month",nyc_df2.reviews_per_month.cast("float"))
nyc_df2=nyc_df2.withColumn("calculated_host_listings_count",\
    nyc_df2.calculated_host_listings_count.cast("int"))
nyc_df2=nyc_df2.withColumn("availability_365",nyc_df2.availability_365.cast("int"))
nyc_df2=nyc_df2.withColumn("last_review",nyc_df2.last_review.cast("date"))

##### Updated data Schema

In [0]:
nyc_df2.printSchema()

root
 |-- id: integer (nullable = true)
 |-- name: string (nullable = true)
 |-- host_id: integer (nullable = true)
 |-- host_name: string (nullable = true)
 |-- neighbourhood_group: string (nullable = true)
 |-- neighbourhood: string (nullable = true)
 |-- latitude: string (nullable = true)
 |-- longitude: string (nullable = true)
 |-- room_type: string (nullable = true)
 |-- price: integer (nullable = true)
 |-- minimum_nights: integer (nullable = true)
 |-- number_of_reviews: integer (nullable = true)
 |-- last_review: date (nullable = true)
 |-- reviews_per_month: float (nullable = true)
 |-- calculated_host_listings_count: integer (nullable = true)
 |-- availability_365: integer (nullable = true)



In [0]:
nyc_df2.display()

id name host_id host_name neighbourhood_group neighbourhood latitude longitude room_type price minimum_nights number_of_reviews last_review reviews_per_month calculated_host_listings_count availability_365 2539 Clean & quiet apt home by the park 2787 John Brooklyn Kensington 40.64749 -73.97237 Private room 149 1 9 2018-10-19 0.21 6 365 2595 Skylit Midtown Castle 2845 Jennifer Manhattan Midtown 40.75362 -73.98377 Entire home/apt 225 1 45 2019-05-21 0.38 2 355 3831 Cozy Entire Floor of Brownstone 4869 LisaRoxanne Brooklyn Clinton Hill 40.68514 -73.95976 Entire home/apt 89 1 270 2019-07-05 4.64 1 194 5022 Entire Apt: Spacious Studio/Loft by central park 7192 Laura Manhattan East Harlem 40.79851 -73.94399 Entire home/apt 80 10 9 2018-11-19 0.1 1 0 5099 Large Cozy 1 BR Apartment In Midtown East 7322 Chris Manhattan Murray Hill 40.74767 -73.975 Entire home/apt 200 3 74 2019-06-22 0.59 1 129 5121 BlissArtsSpace! 7356 Garon Brooklyn Bedford-Stuyvesant 40.68688 -73.95596 Private room 60 45 49 2017-10-05 0.4 1 0 5178 Large Furnished Room Near B'way 8967 Shunichi Manhattan Hell's Kitchen 40.76489 -73.98493 Private room 79 2 430 2019-06-24 3.47 1 220 5203 Cozy Clean Guest Room - Family Apt 7490 MaryEllen Manhattan Upper West Side 40.80178 -73.96723 Private room 79 2 118 2017-07-21 0.99 1 0 5238 Cute & Cozy Lower East Side 1 bdrm 7549 Ben Manhattan Chinatown 40.71344 -73.99037 Entire home/apt 150 1 160 2019-06-09 1.33 4 188 5295 Beautiful 1br on Upper West Side 7702 Lena Manhattan Upper West Side 40.80316 -73.96545 Entire home/apt 135 5 53 2019-06-22 0.43 1 6 5441 Central Manhattan/near Broadway 7989 Kate Manhattan Hell's Kitchen 40.76076 -73.98867 Private room 85 2 188 2019-06-23 1.5 1 39 5803 Lovely Room 1, Garden, Best Area, Legal rental 9744 Laurie Brooklyn South Slope 40.66829 -73.98779 Private room 89 4 167 2019-06-24 1.34 3 314 6021 Wonderful Guest Bedroom in Manhattan for SINGLES 11528 Claudio Manhattan Upper West Side 40.79826 -73.96113 Private room 85 2 113 2019-07-05 0.91 1 333 6090 West Village Nest - Superhost 11975 Alina Manhattan West Village 40.7353 -74.00525 Entire home/apt 120 90 27 2018-10-31 0.22 1 0 6848 Only 2 stops to Manhattan studio 15991 Allen & Irina Brooklyn Williamsburg 40.70837 -73.95352 Entire home/apt 140 2 148 2019-06-29 1.2 1 46 7097 Perfect for Your Parents + Garden 17571 Jane Brooklyn Fort Greene 40.69169 -73.97185 Entire home/apt 215 2 198 2019-06-28 1.72 1 321 7322 Chelsea Perfect 18946 Doti Manhattan Chelsea 40.74192 -73.99501 Private room 140 1 260 2019-07-01 2.12 1 12 7726 Hip Historic Brownstone Apartment with Backyard 20950 Adam And Charity Brooklyn Crown Heights 40.67592 -73.94694 Entire home/apt 99 3 53 2019-06-22 4.44 1 21 7801 Sweet and Spacious Brooklyn Loft 21207 Chaya Brooklyn Williamsburg 40.71842 -73.95718 Entire home/apt 299 3 9 2011-12-28 0.07 1 0 8024 CBG CtyBGd HelpsHaiti rm#1:1-4 22486 Lisel Brooklyn Park Slope 40.68069 -73.97706 Private room 130 2 130 2019-07-01 1.09 6 347 8025 CBG Helps Haiti Room#2.5 22486 Lisel Brooklyn Park Slope 40.67989 -73.97798 Private room 80 1 39 2019-01-01 0.37 6 364 8110 CBG Helps Haiti Rm #2 22486 Lisel Brooklyn Park Slope 40.68001 -73.97865 Private room 110 2 71 2019-07-02 0.61 6 304 8490 MAISON DES SIRENES1,bohemian apartment 25183 Nathalie Brooklyn Bedford-Stuyvesant 40.68371 -73.94028 Entire home/apt 120 2 88 2019-06-19 0.73 2 233 8505 Sunny Bedroom Across Prospect Park 25326 Gregory Brooklyn Windsor Terrace 40.65599 -73.97519 Private room 60 1 19 2019-06-23 1.37 2 85 9357 Midtown Pied-a-terre 30193 Tommi Manhattan Hell's Kitchen 40.76715 -73.98533 Entire home/apt 150 10 58 2017-08-13 0.49 1 75 9518 SPACIOUS, LOVELY FURNISHED MANHATTAN BEDROOM 31374 Shon Manhattan Inwood 40.86482 -73.92106 Private room 44 3 108 2019-06-15 1.11 3 311 9657 Modern 1 BR / NYC / EAST VILLAGE 21904 Dana Manhattan East Village 40.7292 -73.98542 Entire home/apt 180 14 29 2019-04-19 0.24 1 67 9668 front room/double bed 32294 Ssameer Or Trip Manhattan Harlem 40.82245 -73.9510

# Data Visualisation

#### 1) Price of different types of rooms

In [0]:
from pyspark.sql.functions import min,max,avg
nyc_df3=nyc_df2.na.drop("any")
nyc_df4=nyc_df3.filter(nyc_df3["price"] != "0")#.show()
nyc_df4.groupBy("room_type").agg(min("price"),max("price"),avg("price")).display()

room_type min(price) max(price) avg(price) Shared room 10 1800 63.30202140309156 Entire home/apt 10 10000 196.40856818518336 Private room 10 10000 84.04077448747152

Databricks visualization. Run in Databricks to view.

#### 2) Room Preference in different neighbourhood groups

In [0]:
nyc_df3.groupBy("neighbourhood_group","room_type").count().display()

neighbourhood_group room_type count Staten Island Private room 156 Brooklyn Private room 7967 Bronx Entire home/apt 305 Queens Shared room 151 Manhattan Entire home/apt 9938 Manhattan Private room 6272 Manhattan Shared room 354 Bronx Shared room 43 Queens Private room 2656 Queens Entire home/apt 1731 Bronx Private room 516 Staten Island Entire home/apt 150 Brooklyn Entire home/apt 8138 Brooklyn Shared room 290 Staten Island Shared room 5

Databricks visualization. Run in Databricks to view.

#### 3) Total booking in each neighbourhood group

In [0]:
nyc_df3.groupBy("neighbourhood_group").count().display()

neighbourhood_group count Queens 4538 Brooklyn 16395 Staten Island 311 Manhattan 16564 Bronx 864

Databricks visualization. Run in Databricks to view.

#### 4) Number of reviews in each neighbourhood group

In [0]:
nyc_df3.groupBy("neighbourhood_group").sum("number_of_reviews").display()

neighbourhood_group sum(number_of_reviews) Queens 155539 Brooklyn 485177 Staten Island 11337 Manhattan 451959 Bronx 27938

Databricks visualization. Run in Databricks to view.

#### 5) Reviews VS Price in different neighbourhood groups

In [0]:
nyc_df3.groupBy("neighbourhood_group").agg(avg("price"),avg("reviews_per_month")).display()

neighbourhood_group avg(price) avg(reviews_per_month) Queens 95.83494931687969 1.9340105775075502 Brooklyn 121.48752668496493 1.28222384829916 Staten Island 90.42443729903538 1.8523794169570664 Manhattan 180.192948563149 1.2680071237366812 Bronx 79.74768518518519 1.8309953738676592

Databricks visualization. Run in Databricks to view.

##### From above plot, we can see that "Manhattan" group have least number of reviews despite of having expensive rooms

#### 6) Availability of rooms in different neighbourhood groups

In [0]:
nyc_df3.select(["neighbourhood_group","availability_365"]).display()

neighbourhood_group availability_365 Brooklyn 365 Manhattan 355 Brooklyn 194 Manhattan 0 Manhattan 129 Brooklyn 0 Manhattan 220 Manhattan 0 Manhattan 188 Manhattan 6 Manhattan 39 Brooklyn 314 Manhattan 333 Manhattan 0 Brooklyn 46 Brooklyn 321 Manhattan 12 Brooklyn 21 Brooklyn 0 Brooklyn 347 Brooklyn 364 Brooklyn 304 Brooklyn 233 Brooklyn 85 Manhattan 75 Manhattan 311 Manhattan 67 Manhattan 355 Manhattan 255 Brooklyn 284 Manhattan 359 Brooklyn 269 Brooklyn 340 Brooklyn 22 Manhattan 188 Manhattan 96 Brooklyn 345 Brooklyn 311 Manhattan 273 Manhattan 309 Brooklyn 95 Queens 215 Brooklyn 265 Brooklyn 0 Brooklyn 192 Brooklyn 251 Manhattan 302 Brooklyn 140 Brooklyn 234 Manhattan 257 Brooklyn 30 Manhattan 301 Manhattan 294 Brooklyn 320 Manhattan 154 Brooklyn 263 Manhattan 180 Manhattan 231 Brooklyn 297 Brooklyn 292 Manhattan 191 Brooklyn 0 Manhattan 72 Brooklyn 362 Manhattan 336 Manhattan 215 Manhattan 116 Manhattan 88 Manhattan 336 Brooklyn 304 Manhattan 224 Manhattan 322 Queens 324 Brooklyn 132 Manhattan 295 Brooklyn 238 Manhattan 209 Manhattan 328 Brooklyn 38 Manhattan 188 Brooklyn 7 Brooklyn 272 Manhattan 26 Manhattan 0 Brooklyn 288 Brooklyn 317 Brooklyn 207 Brooklyn 185 Brooklyn 158 Brooklyn 0 Brooklyn 9 Manhattan 198 Manhattan 365 Manhattan 364 Brooklyn 311 Manhattan 219 Brooklyn 342 Manhattan 312 Manhattan 243 Brooklyn 152 Brooklyn 9 Brooklyn 137 Brooklyn 222 Manhattan 346 Brooklyn 208 Manhattan 279 Brooklyn 250 Manhattan 164 Brooklyn 192 Manhattan 298 Manhattan 260 Brooklyn 107 Manhattan 199 Manhattan 299 Brooklyn 20 Manhattan 318 Brooklyn 216 Manhattan 224 Manhattan 0 Brooklyn 324 Brooklyn 245 Manhattan 189 Manhattan 307 Brooklyn 310 Manhattan 213 Brooklyn 278 Manhattan 209 Brooklyn 0 Manhattan 16 Manhattan 234 Manhattan 12 Brooklyn 178 Brooklyn 275 Brooklyn 163 Brooklyn 365 Brooklyn 34 Brooklyn 280 Brooklyn 0 Queens 1 Brooklyn 170 Brooklyn 188 Brooklyn 214 Manhattan 248 Brooklyn 262 Brooklyn 280 Manhattan 307 Brooklyn 339 Brooklyn 1 Brooklyn 269 Manhattan 10 Manhattan 312 Brooklyn 189 Manhattan 290 Brooklyn 230 Manhattan 164 Brooklyn 53 Queens 126 Brooklyn 3 Brooklyn 189 Manhattan 365 Brooklyn 0 Manhattan 0 Brooklyn 336 Brooklyn 342 Staten Island 312 Brooklyn 37 Bronx 353 Brooklyn 177 Manhattan 310 Manhattan 0 Brooklyn 321 Manhattan 246 Manhattan 231 Manhattan 225 Manhattan 0 Brooklyn 0 Queens 365 Manhattan 233 Brooklyn 1 Brooklyn 18 Brooklyn 343 Brooklyn 250 Manhattan 326 Brooklyn 364 Manhattan 0 Manhattan 299 Manhattan 207 Brooklyn 162 Manhattan 7 Manhattan 328 Queens 365 Manhattan 0 Brooklyn 0 Queens 240 Queens 365 Queens 365 Brooklyn 164 Manhattan 363 Brooklyn 250 Manhattan 247 Bronx 323 Manhattan 192 Brooklyn 125 Brooklyn 91 Manhattan 75 Manhattan 286 Brooklyn 60 Brooklyn 0 Manhattan 192 Brooklyn 58 Manhattan 245 Queens 292 Brooklyn 279 Manhattan 0 Manhattan 3 Manhattan 351 Manhattan 201 Manhattan 232 Manhattan 258 Brooklyn 272 Manhattan 341 Manhattan 244 Queens 365 Brooklyn 12 Manhattan 265 Manhattan 0 Manhattan 329 Manhattan 91 Manhattan 365 Manhattan 253 Manhattan 365 Manhattan 320 Manhattan 0 Manhattan 192 Manhattan 0 Manhattan 348 Manhattan 0 Manhattan 353 Manhattan 140 Brooklyn 2 Manhattan 56 Brooklyn 68 Staten Island 360 Staten Island 0 Staten Island 320 Manhattan 326 Manhattan 76 Brooklyn 279 Brooklyn 15 Staten Island 340 Queens 226 Brooklyn 365 Brooklyn 0 Bronx 365 Brooklyn 11 Manhattan 316 Brooklyn 281 Brooklyn 362 Brooklyn 301 Brooklyn 189 Brooklyn 0 Brooklyn 287 Manhattan 14 Manhattan 86 Manhattan 261 Brooklyn 68 Manhattan 231 Brooklyn 152 Brooklyn 46 Manhattan 364 Brooklyn 246 Brooklyn 288 Brooklyn 331 Manhattan 51 Manhattan 364 Brooklyn 254 Manhattan 189 Brooklyn 263 Brooklyn 258 Manhattan 103 Brooklyn 42 Manhattan 246 Manhattan 364 Manhattan 318 Brooklyn 72 Manhattan 249 Brooklyn 272 Brooklyn 325 Manhattan 298 Manhattan 35 Brooklyn 203 Manhattan 132 Manhattan 5 Manhattan 297 Manhattan 276 Manhattan 102 Manhattan 251 Brooklyn 188 Bronx 346 Manhattan 0 Brooklyn 15 Brooklyn 71 Brooklyn 215 Manhattan 253 Manha

Databricks visualization. Run in Databricks to view.

#### 7) Availability in different places

In [0]:
nyc_df2.select(["neighbourhood_group","neighbourhood","availability_365"]).display()

neighbourhood_group neighbourhood availability_365 Brooklyn Kensington 365 Manhattan Midtown 355 Brooklyn Clinton Hill 194 Manhattan East Harlem 0 Manhattan Murray Hill 129 Brooklyn Bedford-Stuyvesant 0 Manhattan Hell's Kitchen 220 Manhattan Upper West Side 0 Manhattan Chinatown 188 Manhattan Upper West Side 6 Manhattan Hell's Kitchen 39 Brooklyn South Slope 314 Manhattan Upper West Side 333 Manhattan West Village 0 Brooklyn Williamsburg 46 Brooklyn Fort Greene 321 Manhattan Chelsea 12 Brooklyn Crown Heights 21 Brooklyn Williamsburg 0 Brooklyn Park Slope 347 Brooklyn Park Slope 364 Brooklyn Park Slope 304 Brooklyn Bedford-Stuyvesant 233 Brooklyn Windsor Terrace 85 Manhattan Hell's Kitchen 75 Manhattan Inwood 311 Manhattan East Village 67 Manhattan Harlem 355 Manhattan Harlem 255 Brooklyn Greenpoint 284 Manhattan Harlem 359 Brooklyn Bedford-Stuyvesant 269 Brooklyn South Slope 340 Brooklyn Bushwick 22 Manhattan Lower East Side 188 Manhattan East Village 96 Brooklyn South Slope 345 Brooklyn Fort Greene 311 Manhattan Upper West Side 273 Manhattan Harlem 309 Brooklyn Prospect-Lefferts Gardens 95 Queens Long Island City 215 Brooklyn Bedford-Stuyvesant 265 Brooklyn Bedford-Stuyvesant 0 Brooklyn Fort Greene 192 Brooklyn Bedford-Stuyvesant 251 Manhattan Upper West Side 302 Brooklyn Williamsburg 140 Brooklyn Greenpoint 234 Manhattan Kips Bay 257 Brooklyn Williamsburg 30 Manhattan Lower East Side 301 Manhattan Hell's Kitchen 294 Brooklyn Greenpoint 320 Manhattan SoHo 154 Brooklyn Williamsburg 263 Manhattan Chelsea 180 Manhattan Upper East Side 231 Brooklyn Prospect Heights 297 Brooklyn Clinton Hill 292 Manhattan Hell's Kitchen 191 Brooklyn Park Slope 0 Manhattan East Village 72 Brooklyn Williamsburg 362 Manhattan East Village 336 Manhattan East Harlem 215 Manhattan East Village 116 Manhattan Hell's Kitchen 88 Manhattan Washington Heights 336 Brooklyn Clinton Hill 304 Manhattan East Village 224 Manhattan Upper East Side 322 Queens Woodside 324 Brooklyn Fort Greene 132 Manhattan Chelsea 295 Brooklyn Williamsburg 238 Manhattan Harlem 209 Manhattan Lower East Side 328 Brooklyn Flatbush 38 Manhattan Lower East Side 188 Brooklyn Brooklyn Heights 7 Brooklyn Williamsburg 272 Manhattan East Village 26 Manhattan East Village 0 Brooklyn Williamsburg 288 Brooklyn Bushwick 317 Brooklyn Prospect Heights 207 Brooklyn Clinton Hill 185 Brooklyn Prospect Heights 158 Brooklyn Williamsburg 0 Brooklyn Bushwick 9 Manhattan Upper West Side 198 Manhattan Harlem 365 Manhattan Chelsea 364 Brooklyn Bedford-Stuyvesant 311 Manhattan Harlem 219 Brooklyn Carroll Gardens 342 Manhattan Washington Heights 312 Manhattan West Village 243 Brooklyn Williamsburg 152 Brooklyn Park Slope 9 Brooklyn Bedford-Stuyvesant 137 Brooklyn Williamsburg 222 Manhattan Harlem 346 Brooklyn Gowanus 208 Manhattan Hell's Kitchen 279 Brooklyn Clinton Hill 250 Manhattan East Village 164 Brooklyn South Slope 192 Manhattan East Village 298 Manhattan Kips Bay 260 Brooklyn Williamsburg 107 Manhattan Upper West Side 199 Manhattan East Village 299 Brooklyn South Slope 20 Manhattan Harlem 318 Brooklyn South Slope 216 Manhattan Upper West Side 224 Manhattan East Village 0 Brooklyn Prospect-Lefferts Gardens 324 Brooklyn Williamsburg 245 Manhattan Upper East Side 189 Manhattan Washington Heights 307 Brooklyn Bedford-Stuyvesant 310 Manhattan Harlem 213 Brooklyn Clinton Hill 278 Manhattan East Village 209 Brooklyn Greenpoint 0 Manhattan Lower East Side 16 Manhattan Hell's Kitchen 234 Manhattan West Village 12 Brooklyn Flatlands 178 Brooklyn Clinton Hill 275 Brooklyn Bedford-Stuyvesant 163 Brooklyn Clinton Hill 365 Brooklyn Greenpoint 34 Brooklyn Williamsburg 280 Brooklyn Cobble Hill 0 Queens Flushing 1 Brooklyn Bedford-Stuyvesant 170 Brooklyn Williamsburg 188 Brooklyn Williamsburg 214 Manhattan East Village 248 Brooklyn Williamsburg 262 Brooklyn Fort Greene 280 Manhattan West Village 307 Brooklyn Prospect Heights 339 Brooklyn Williamsburg 1 Brooklyn Prospect Heights 269 Manhattan East Harlem 10 Manhattan Wes

Databricks visualization. Run in Databricks to view.

#### 8) Average reviews per year

In [0]:
from pyspark.sql.functions import year
year_df=nyc_df3.select(["number_of_reviews",year("last_review").alias("last_review_year")])
year_df.groupBy("last_review_year").avg("number_of_reviews").display()

last_review_year avg(number_of_reviews) 2018 11.962042101773578 2015 4.128242074927954 2013 5.041666666666667 2014 4.683417085427136 2019 40.20894331644661 2012 7.12 2016 5.982975573649148 2011 8.714285714285714 2017 8.895970009372071

Databricks visualization. Run in Databricks to view.

#### 9) Preferred room type

In [0]:
nyc_df3.groupBy("room_type").count().display()

room_type count Shared room 843 Entire home/apt 20262 Private room 17567

Databricks visualization. Run in Databricks to view.

#### 10) Minimum Nights spent in each room type

In [0]:
nyc_df3.groupBy("room_type").avg('minimum_nights').display()

room_type avg(minimum_nights) Shared room 4.406880189798339 Entire home/apt 7.091254565195933 Private room 4.548414641088405

Databricks visualization. Run in Databricks to view.

#### 11) Comparing host_listings_count of different sites of Airbnb

In [0]:
nyc_df3.select("neighbourhood_group","neighbourhood","calculated_host_listings_count").display()

neighbourhood_group neighbourhood calculated_host_listings_count Brooklyn Kensington 6 Manhattan Midtown 2 Brooklyn Clinton Hill 1 Manhattan East Harlem 1 Manhattan Murray Hill 1 Brooklyn Bedford-Stuyvesant 1 Manhattan Hell's Kitchen 1 Manhattan Upper West Side 1 Manhattan Chinatown 4 Manhattan Upper West Side 1 Manhattan Hell's Kitchen 1 Brooklyn South Slope 3 Manhattan Upper West Side 1 Manhattan West Village 1 Brooklyn Williamsburg 1 Brooklyn Fort Greene 1 Manhattan Chelsea 1 Brooklyn Crown Heights 1 Brooklyn Williamsburg 1 Brooklyn Park Slope 6 Brooklyn Park Slope 6 Brooklyn Park Slope 6 Brooklyn Bedford-Stuyvesant 2 Brooklyn Windsor Terrace 2 Manhattan Hell's Kitchen 1 Manhattan Inwood 3 Manhattan East Village 1 Manhattan Harlem 3 Manhattan Harlem 1 Brooklyn Greenpoint 3 Manhattan Harlem 3 Brooklyn Bedford-Stuyvesant 2 Brooklyn South Slope 3 Brooklyn Bushwick 2 Manhattan Lower East Side 4 Manhattan East Village 2 Brooklyn South Slope 1 Brooklyn Fort Greene 1 Manhattan Upper West Side 1 Manhattan Harlem 1 Brooklyn Prospect-Lefferts Gardens 1 Queens Long Island City 1 Brooklyn Bedford-Stuyvesant 1 Brooklyn Bedford-Stuyvesant 1 Brooklyn Fort Greene 2 Brooklyn Bedford-Stuyvesant 3 Manhattan Upper West Side 1 Brooklyn Williamsburg 1 Brooklyn Greenpoint 1 Manhattan Kips Bay 1 Brooklyn Williamsburg 1 Manhattan Lower East Side 1 Manhattan Hell's Kitchen 2 Brooklyn Greenpoint 3 Manhattan SoHo 1 Brooklyn Williamsburg 1 Manhattan Chelsea 1 Manhattan Upper East Side 2 Brooklyn Prospect Heights 2 Brooklyn Clinton Hill 2 Manhattan Hell's Kitchen 1 Brooklyn Park Slope 1 Manhattan East Village 2 Brooklyn Williamsburg 1 Manhattan East Village 2 Manhattan East Harlem 1 Manhattan East Village 1 Manhattan Hell's Kitchen 1 Manhattan Washington Heights 2 Brooklyn Clinton Hill 1 Manhattan East Village 1 Manhattan Upper East Side 1 Queens Woodside 1 Brooklyn Fort Greene 1 Manhattan Chelsea 1 Brooklyn Williamsburg 4 Manhattan Harlem 1 Manhattan Lower East Side 1 Brooklyn Flatbush 1 Manhattan Lower East Side 1 Brooklyn Brooklyn Heights 1 Brooklyn Williamsburg 1 Manhattan East Village 1 Manhattan East Village 1 Brooklyn Williamsburg 4 Brooklyn Bushwick 1 Brooklyn Prospect Heights 1 Brooklyn Clinton Hill 6 Brooklyn Prospect Heights 1 Brooklyn Williamsburg 1 Brooklyn Bushwick 2 Manhattan Upper West Side 1 Manhattan Harlem 1 Manhattan Chelsea 2 Brooklyn Bedford-Stuyvesant 2 Manhattan Harlem 3 Brooklyn Carroll Gardens 3 Manhattan Washington Heights 1 Manhattan West Village 2 Brooklyn Williamsburg 1 Brooklyn Park Slope 1 Brooklyn Bedford-Stuyvesant 2 Brooklyn Williamsburg 1 Manhattan Harlem 1 Brooklyn Gowanus 1 Manhattan Hell's Kitchen 2 Brooklyn Clinton Hill 6 Manhattan East Village 1 Brooklyn South Slope 2 Manhattan East Village 4 Manhattan Kips Bay 1 Brooklyn Williamsburg 1 Manhattan Upper West Side 1 Manhattan East Village 4 Brooklyn South Slope 3 Manhattan Harlem 1 Brooklyn South Slope 2 Manhattan Upper West Side 1 Manhattan East Village 1 Brooklyn Prospect-Lefferts Gardens 1 Brooklyn Williamsburg 1 Manhattan Upper East Side 1 Manhattan Washington Heights 1 Brooklyn Bedford-Stuyvesant 2 Manhattan Harlem 3 Brooklyn Clinton Hill 1 Manhattan East Village 1 Brooklyn Greenpoint 1 Manhattan Lower East Side 1 Manhattan Hell's Kitchen 3 Manhattan West Village 1 Brooklyn Flatlands 1 Brooklyn Clinton Hill 3 Brooklyn Bedford-Stuyvesant 2 Brooklyn Clinton Hill 3 Brooklyn Greenpoint 1 Brooklyn Williamsburg 1 Brooklyn Cobble Hill 1 Queens Flushing 1 Brooklyn Bedford-Stuyvesant 2 Brooklyn Williamsburg 1 Brooklyn Williamsburg 1 Manhattan East Village 1 Brooklyn Williamsburg 4 Brooklyn Fort Greene 5 Manhattan West Village 1 Brooklyn Prospect Heights 1 Brooklyn Williamsburg 1 Brooklyn Prospect Heights 1 Manhattan East Harlem 1 Manhattan West Village 1 Brooklyn Williamsburg 1 Manhattan Upper East Side 2 Brooklyn Boerum Hill 1 Manhattan Upper East Side 2 Brooklyn Williamsburg 2 Queens Sunnyside 1 Brooklyn Bedford-Stuyvesant 2 Brooklyn DUMBO 1 Manhattan Upper East Side

Databricks visualization. Run in Databricks to view.

# Thank You !